In [1]:
#The original code developed by Haixu Wu, available on GitHub, was adapted by the authors, with Ling Feng leading the adaptation, to meet the requirements of the experiments.
#
#All modifications to the original code were made in accordance with the MIT License below:
#
#MIT License
#
#Copyright (c) 2021 THUML @ Tsinghua University
#
#Permission is hereby granted, free of charge, to any person obtaining a copy of this software and associated 
#documentation files (the "Software"), to deal in the Software without restriction, including without limitation 
#the rights to use, copy, modify, merge, publish, distribute, sublicense, and/or sell copies of the Software, 
#and to permit persons to whom the Software is furnished to do so, subject to the following conditions:
#
#The above copyright notice and this permission notice shall be included in all copies or substantial portions of the Software.
#
#THE SOFTWARE IS PROVIDED "AS IS", WITHOUT WARRANTY OF ANY KIND, EXPRESS OR IMPLIED, INCLUDING BUT NOT LIMITED TO 
#THE WARRANTIES OF MERCHANTABILITY, FITNESS FOR A PARTICULAR PURPOSE AND NONINFRINGEMENT. IN NO EVENT SHALL THE AUTHORS 
#OR COPYRIGHT HOLDERS BE LIABLE FOR ANY CLAIM, DAMAGES OR OTHER LIABILITY, WHETHER IN AN ACTION OF CONTRACT, TORT OR 
#OTHERWISE, ARISING FROM, OUT OF OR IN CONNECTION WITH THE SOFTWARE OR THE USE OR OTHER DEALINGS IN THE SOFTWARE.

In [1]:
import argparse
import random
import os
import matplotlib.pyplot as plt
import numpy as np
import torch
from utils.tools import dotdict
from exp.exp_main import Exp_Main
import sys

In [5]:
fix_seed = 2021
random.seed(fix_seed)
torch.manual_seed(fix_seed)
np.random.seed(fix_seed)

parser = argparse.ArgumentParser(description='Time Series Forecasting Using CNN Correlation-based Transformer')

# basic config
parser.add_argument('--is_training', type=int, required=True, default=1, help='status')
parser.add_argument('--model_id', type=str, required=True, default='test', help='model id')
parser.add_argument('--model', type=str, required=True, default='CNNCorrelationBasedTransformer',
                        help='model name, there is no option for this, only CNNCorrelationBasedTransformer available')
# data loader
parser.add_argument('--data', type=str, required=True, default='custom', help='dataset type')
parser.add_argument('--root_path', type=str, default='./data/', help='root path of the data file')
parser.add_argument('--data_path', type=str, default='set2024.csv', help='data file')
parser.add_argument('--features', type=str, default='MS',
                        help='forecasting task, options:[M, S, MS]; M:multivariate predict multivariate, S:univariate predict univariate, MS:multivariate predict univariate')
parser.add_argument('--target', type=str, default='OT', help='target feature in S or MS task')
parser.add_argument('--freq', type=str, default='d',
                        help='freq for time features encoding, options:[s:secondly, t:minutely, h:hourly, d:daily, b:business days, w:weekly, m:monthly], you can also use more detailed freq like 15min or 3h')
parser.add_argument('--checkpoints', type=str, default='./checkpoints/', help='location of model checkpoints')

# forecasting task
parser.add_argument('--seq_len', type=int, default=10, help='input sequence length')
parser.add_argument('--label_len', type=int, default=10, help='start token length')
parser.add_argument('--pred_len', type=int, default=5, help='prediction sequence length')

# model define
parser.add_argument('--enc_in', type=int, default=4, help='encoder input size')
parser.add_argument('--dec_in', type=int, default=4, help='decoder input size')
parser.add_argument('--c_out', type=int, default=1, help='output size')
parser.add_argument('--cnn_out_channels', type=int, default=512, help='dimension of CNN')
parser.add_argument('--d_model', type=int, default=512, help='dimension of model')
parser.add_argument('--n_heads', type=int, default=4, help='num of heads')
parser.add_argument('--e_layers', type=int, default=2, help='num of encoder layers')
parser.add_argument('--d_layers', type=int, default=1, help='num of decoder layers')
parser.add_argument('--d_ff', type=int, default=2048, help='dimension of fcn')
parser.add_argument('--moving_avg', type=int, default=35, help='window size of moving average')
parser.add_argument('--factor', type=int, default=4, help='attn factor')
parser.add_argument('--distil', action='store_false', 
                    help='whether to use distilling in encoder, using this argument means not using distilling', 
                    default=True)
parser.add_argument('--dropout', type=float, default=0.05, help='dropout')
parser.add_argument('--embed', type=str, default='timeF',
                        help='time features encoding, options:[timeF, fixed, learned]')
parser.add_argument('--activation', type=str, default='gelu', help='activation')
parser.add_argument('--output_attention', action='store_true', help='whether to output attention in encoder')
parser.add_argument('--do_predict', action='store_true', help='whether to predict unseen future data')

# optimization
parser.add_argument('--num_workers', type=int, default=0, help='data loader num workers')
parser.add_argument('--itr', type=int, default=2, help='experiments times')
parser.add_argument('--train_epochs', type=int, default=30, help='train epochs')
parser.add_argument('--batch_size', type=int, default=8, help='batch size of train input data')
parser.add_argument('--patience', type=int, default=20, help='early stopping patience')
parser.add_argument('--learning_rate', type=float, default=0.0001, help='optimizer learning rate')
parser.add_argument('--des', type=str, default='test', help='exp description')
parser.add_argument('--loss', type=str, default='mse', help='loss function')
parser.add_argument('--lradj', type=str, default='type1', help='adjust learning rate')
parser.add_argument('--use_amp', action='store_true', help='use automatic mixed precision training', default=False)

# GPU
parser.add_argument('--use_gpu', type=bool, default=True, help='use gpu')
parser.add_argument('--gpu', type=int, default=0, help='gpu')
parser.add_argument('--use_multi_gpu', action='store_true', help='use multiple gpus', default=False)
parser.add_argument('--devices', type=str, default='0,1,2,3', help='device ids of multile gpus')

sys.argv = ['TSF Using CBT', '--is_training', '1', '--model_id', 'test', '--model', 'CNNCorrelationBasedTransformer',
               '--data', 'custom',
               '--root_path', './data/', 
               '--data_path', 'set2024.csv', 
               '--features', 'MS', 
               '--target', 'OT', 
               '--freq', 'd', 
               '--checkpoints', './checkpoints/', 
               '--seq_len', '10', 
               '--label_len', '10',
               '--pred_len', '5', 
               '--enc_in', '4', 
               '--dec_in', '4', 
               '--c_out', '1', 
               '--cnn_out_channels', '128',
               '--d_model', '512', 
               '--n_heads', '4', 
               '--e_layers', '2',
               '--d_layers', '1', 
               '--d_ff', '2048',
               '--moving_avg', '35', 
               '--factor', '4', 
               '--distil', 
               '--dropout', '0.05', 
               '--embed', 'timeF', 
               '--activation', 'gelu',
               '--output_attention',  
               '--do_predict',
               '--num_workers', '0', 
               '--itr', '2', 
               '--train_epochs', '30', 
               '--batch_size', '8', 
               '--patience', '20', 
               '--learning_rate', '0.0001', 
               '--des', 'test', 
               '--loss', 'mse',
               '--lradj', 'type1', 
               '--use_amp', 
               '--use_gpu', False, #True,
               '--gpu', '0',
               '--use_multi_gpu', 
               '--devices', '0'
               ]
    
args = parser.parse_args()

args.use_gpu = True if torch.cuda.is_available() and args.use_gpu else False

if args.use_gpu and args.use_multi_gpu:
    args.dvices = args.devices.replace(' ', '')
    device_ids = args.devices.split(',')
    args.device_ids = [int(id_) for id_ in device_ids]
    args.gpu = args.device_ids[0]

print('Args in experiment:')
print(args)

#import CNNCorrelationBasedTransformer
# Load pre-trained model
#model = CNNCorrelationBasedTransformer.Model(args)
#checkpoint_path = './checkpoints/test_CNNCorrelationBasedTransformer_custom_ftMS_sl10_ll10_pl5_dm512_nh4_el2_dl1_df2048_fc4_ebtimeF_dtFalse_test_1/checkpoint.pth'
#model.load_state_dict(torch.load(checkpoint_path))

# Freeze encoder layers
#for param in model.encoder.parameters():
#    param.requires_grad = False
#for name, param in model.named_parameters():
#    if 'EncoderLayer.0' in name:
#        param.requires_grad = False

Exp = Exp_Main

if args.is_training:
    for ii in range(args.itr):
        # setting record of experiments
        setting = '{}_{}_{}_ft{}_sl{}_ll{}_pl{}_dcc{}_dm{}_nh{}_el{}_dl{}_df{}_fc{}_eb{}_dt{}_{}_{}'.format(
            args.model_id,
            args.model,
            args.data,
            args.features,
            args.seq_len,
            args.label_len,
            args.pred_len,
            args.cnn_out_channels,
            args.d_model,
            args.n_heads,
            args.e_layers,
            args.d_layers,
            args.d_ff,
            args.factor,
            args.embed,
            args.distil,
            args.des, ii)

        exp = Exp(args)  # set experiments
        print('>>>>>>>start training : {}>>>>>>>>>>>>>>>>>>>>>>>>>>'.format(setting))
        exp.train(setting)

        print('>>>>>>>testing : {}<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<'.format(setting))
        exp.test(setting)

        if args.do_predict:
            print('>>>>>>>predicting : {}<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<'.format(setting))
            exp.predict(setting, True)

        torch.cuda.empty_cache()
else:
    ii = 0
    setting = '{}_{}_{}_ft{}_sl{}_ll{}_pl{}_dcc{}_dm{}_nh{}_el{}_dl{}_df{}_fc{}_eb{}_dt{}_{}_{}'.format(args.model_id,
                                                                                                    args.model,
                                                                                                    args.data,
                                                                                                    args.features,
                                                                                                    args.seq_len,
                                                                                                    args.label_len,
                                                                                                    args.pred_len,
                                                                                                    args.cnn_out_channels,
                                                                                                    args.d_model,
                                                                                                    args.n_heads,
                                                                                                    args.e_layers,
                                                                                                    args.d_layers,
                                                                                                    args.d_ff,
                                                                                                    args.factor,
                                                                                                    args.embed,
                                                                                                    args.distil,
                                                                                                    args.des, ii)

    exp = Exp(args)  # set experiments
    print('>>>>>>>testing : {}<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<'.format(setting))
    exp.test(setting, test=1)
    torch.cuda.empty_cache()


#if __name__ == "__main__":
#        main()

Args in experiment:
Namespace(is_training=1, model_id='test', model='CNNCorrelationBasedTransformer', data='custom', root_path='./data/', data_path='set2024.csv', features='MS', target='OT', freq='d', checkpoints='./checkpoints/', seq_len=10, label_len=10, pred_len=5, enc_in=4, dec_in=4, c_out=1, cnn_out_channels=128, d_model=512, n_heads=4, e_layers=2, d_layers=1, d_ff=2048, moving_avg=35, factor=4, distil=False, dropout=0.05, embed='timeF', activation='gelu', output_attention=True, do_predict=True, num_workers=0, itr=2, train_epochs=30, batch_size=8, patience=20, learning_rate=0.0001, des='test', loss='mse', lradj='type1', use_amp=True, use_gpu=False, gpu=0, use_multi_gpu=True, devices='0')
Use CPU
>>>>>>>start training : test_CNNCorrelationBasedTransformer_custom_ftMS_sl10_ll10_pl5_dcc128_dm512_nh4_el2_dl1_df2048_fc4_ebtimeF_dtFalse_test_0>>>>>>>>>>>>>>>>>>>>>>>>>>
train 492
val 69
test 140
Epoch: 1 cost time: 7.268678188323975
Epoch: 1, Steps: 61 | Train Loss: 0.2599820 Vali Loss: 